In [1]:
import pandas as pd
import numpy as np
from sklearn.neighbors import NearestNeighbors
from scipy.spatial.distance import euclidean

In [2]:
df = pd.read_csv("onehr.csv")

In [3]:
df

date  WSR0  WSR1  WSR2  WSR3  WSR4  WSR5  WSR6  WSR7  WSR8  ...  \
0       1/1/1998   0.8   1.8   2.4   2.1   2.0   2.1   1.5   1.7   1.9  ...   
1       1/2/1998   2.8   3.2   3.3   2.7   3.3   3.2   2.9   2.8   3.1  ...   
2       1/3/1998   2.9   2.8   2.6   2.1   2.2   2.5   2.5   2.7   2.2  ...   
3       1/4/1998   4.7   3.8   3.7   3.8   2.9   3.1   2.8   2.5   2.4  ...   
4       1/5/1998   2.6   2.1   1.6   1.4   0.9   1.5   1.2   1.4   1.3  ...   
...          ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   
2531  12/27/2004   0.3   0.4   0.5   0.5   0.2   0.3   0.4   0.4   1.3  ...   
2532  12/28/2004   1.0   1.4   1.1   1.7   1.5   1.7   1.8   1.5   2.1  ...   
2533  12/29/2004   0.8   0.8   1.2   0.9   0.4   0.6   0.8   1.1   1.5  ...   
2534  12/30/2004   1.3   0.9   1.5   1.2   1.6   1.8   1.1   1.0   1.9  ...   
2535  12/31/2004   1.5   1.3   1.8   1.4   1.2   1.7   1.6   1.4   1.6  ...   

      RH50    U50    V50    HT50     KI     TT      SLP  SLP_  Precp  Class  
0     0.15  10.67  -1.56  5795.0 -12.10  17.90  10330.0 -55.0   0.00      0  
1     0.48   8.39   3.84  5805.0  14.05  29.00  10275.0 -55.0   0.00      0  
2     0.60   6.94   9.80  5790.0  17.90  41.30  10235.0 -40.0   0.00      0  
3     0.49   8.73  10.54  5775.0  31.15  51.70  10195.0 -40.0   2.08      0  
4      NaN    NaN    NaN     NaN    NaN    NaN      NaN   NaN   0.58      0  
...    ...    ...    ...     ...    ...    ...      ...   ...    ...    ...  
2531  0.07   7.93  -4.41  5800.0 -25.60  21.80  10295.0  65.0   0.00      0  
2532  0.04   5.95  -1.14  5845.0 -19.40  19.10  10310.0  15.0   0.00      0  
2533  0.06   7.80  -0.64  5845.0  -9.60  35.20  10275.0 -35.0   0.00      0  
2534  0.25   7.72  -0.89  5845.0 -19.60  34.20  10245.0 -30.0   0.05      0  
2535  0.54  13.07   9.15  5820.0   1.95  39.35  10220.0 -25.0   0.00      0  

[2536 rows x 74 columns]

In [4]:
df.dtypes

date      object
WSR0     float64
WSR1     float64
WSR2     float64
WSR3     float64
          ...   
TT       float64
SLP      float64
SLP_     float64
Precp    float64
Class      int64
Length: 74, dtype: object

In [5]:
df.drop('date', axis=1, inplace=True)

In [6]:
df.isnull().sum()

WSR0     299
WSR1     292
WSR2     294
WSR3     292
WSR4     293
        ... 
TT       125
SLP       95
SLP_     159
Precp      2
Class      0
Length: 73, dtype: int64

In [7]:
null_counts = df.isnull().sum().sum()
total = df.size
null_percentages = 100 * null_counts / total
print("total nilai :",total)
print("nilai hilang :",null_counts)
print("persentase :",null_percentages)

total nilai : 185128
nilai hilang : 14938
persentase : 8.0690117108163


In [8]:
null_counts = df.isnull().sum()
null_percentages = 100 * null_counts / len(df)
null_percentages

WSR0     11.790221
WSR1     11.514196
WSR2     11.593060
WSR3     11.514196
WSR4     11.553628
           ...    
TT        4.929022
SLP       3.746057
SLP_      6.269716
Precp     0.078864
Class     0.000000
Length: 73, dtype: float64

# Imputasi

In [9]:
def jarak(df2,col):
    euc_dist[col] = []
    euc_dist_append =euc_dist[col].append
    for row in range(df2.shape[0]):
        current = df2.index[df2.iloc[:,col] == 0].tolist()
        current = current[0]
        a = df2.iloc[current,col+1:].tolist()
        b = df2.iloc[current,:col].tolist()
        x1 = b+a
        if(row is not current):
            a=df2.iloc[row,col+1:].tolist()
            b=df2.iloc[row,:col].tolist()
            x2=b+a
        else:
            continue
        dist = euclidean(x1,x2)
        euc_dist_append([dist,df2.iloc[row,col]])
#         print(" x1 = ",x1,"\n x2 = ",x2,"\n distance = ",euc_dist[col])

    lst = list(euc_dist[col])
    lst.sort()
    euc_dist[col] = lst
#     print(euc_dist[col])

In [10]:
from collections import Counter
def hitung(val, k, temp=None, i=0, counter=0):
    counts = Counter(val)
    total_count = len(counts)
#     print("jumlah val:", total_count)
    if counter >= int((k/2)+1) and total_count == 1 :
        print("median : ",int((k/2)+1))
        return temp
    elif i is not k:
        if temp is None:
            temp = val[i]
        elif temp != val[i]:
            temp = val[i]
            counter = 0
        # print(f"temp = {temp} , counter = {counter} , i = {i} , k = {k} , median = {int((k/2)+1)}, val[i] = {val[i]}")
        return hitung(val,k,temp,i+1,counter+1)
    else:
        return None
    
def Final(df,col,k):
    terdekat = []
    mean = 0
    std = 0
    diffsquared = 0
    sum_diffsquared = 0
    fuzzy_val = []
    euc_val = []
    terdekat_append = terdekat.append
    fuzzy_append = fuzzy_val.append
    
    for val in range(k):
        terdekat_append(euc_dist[col][val])
    
    for x,y in terdekat:
        mean += y  
        euc_val.append(y)
    mean /= len(terdekat)
    
    print(euc_val)
    
    for x,y in terdekat:
        diffsquared = (y-mean)**2
        sum_diffsquared = diffsquared + sum_diffsquared
    std_dev = ((sum_diffsquared)/len(terdekat))**(1/2)
    print("mean : ",mean)
    print("standar deviasi : ",std_dev)
    
    euc_val.sort()
    fuzzy = hitung(euc_val,3)
    
    for x,y in terdekat:
        if fuzzy is None:
            fuzzy_append((y,gaussian(y,mean,std_dev)))
        else:
            fuzzy_val.append((y,fuzzy))
        
    print("fuzzy : ",fuzzy_val)
    print("fuzzy : ",fuzzy)
    
    pembilang = 0
    penyebut = 0 
    
    for nilai,bobot in fuzzy_val:
        pembilang += nilai*bobot
        penyebut += bobot
            
    print("pembilang : ", pembilang)
    print("penyebut : ",penyebut)
    
    if fuzzy is not None:
        tertimbang = fuzzy
    else:
        tertimbang = pembilang / penyebut
    
    print("rata-rata tertimbang : ",tertimbang)
    index = dummy.index[dummy.iloc[:,col] == 0].tolist()
    index = index[0]
    
    if tertimbang == 0:
        tertimbang = dummy.iloc[index-1, col]
        
    dummy.iloc[index,col] = tertimbang
    print(" ")

In [11]:
def gaussian(val, mean, std_dev):
    gaussian_mf = 2.718**((-1 * (val-mean)**2) / (2 * std_dev**2))
    return gaussian_mf

In [12]:
data = df.iloc[:, :-1]
df2 = data.copy()
dummy = df2.fillna(0)
dummy

WSR0  WSR1  WSR2  WSR3  WSR4  WSR5  WSR6  WSR7  WSR8  WSR9  ...   T50  \
0      0.8   1.8   2.4   2.1   2.0   2.1   1.5   1.7   1.9   2.3  ... -15.5   
1      2.8   3.2   3.3   2.7   3.3   3.2   2.9   2.8   3.1   3.4  ... -14.5   
2      2.9   2.8   2.6   2.1   2.2   2.5   2.5   2.7   2.2   2.5  ... -15.9   
3      4.7   3.8   3.7   3.8   2.9   3.1   2.8   2.5   2.4   3.1  ... -16.8   
4      2.6   2.1   1.6   1.4   0.9   1.5   1.2   1.4   1.3   1.4  ...   0.0   
...    ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   ...   
2531   0.3   0.4   0.5   0.5   0.2   0.3   0.4   0.4   1.3   2.2  ... -12.4   
2532   1.0   1.4   1.1   1.7   1.5   1.7   1.8   1.5   2.1   2.4  ... -12.0   
2533   0.8   0.8   1.2   0.9   0.4   0.6   0.8   1.1   1.5   1.5  ... -11.8   
2534   1.3   0.9   1.5   1.2   1.6   1.8   1.1   1.0   1.9   2.0  ... -10.8   
2535   1.5   1.3   1.8   1.4   1.2   1.7   1.6   1.4   1.6   3.0  ... -11.9   

      RH50    U50    V50    HT50     KI     TT      SLP  SLP_  Precp  
0     0.15  10.67  -1.56  5795.0 -12.10  17.90  10330.0 -55.0   0.00  
1     0.48   8.39   3.84  5805.0  14.05  29.00  10275.0 -55.0   0.00  
2     0.60   6.94   9.80  5790.0  17.90  41.30  10235.0 -40.0   0.00  
3     0.49   8.73  10.54  5775.0  31.15  51.70  10195.0 -40.0   2.08  
4     0.00   0.00   0.00     0.0   0.00   0.00      0.0   0.0   0.58  
...    ...    ...    ...     ...    ...    ...      ...   ...    ...  
2531  0.07   7.93  -4.41  5800.0 -25.60  21.80  10295.0  65.0   0.00  
2532  0.04   5.95  -1.14  5845.0 -19.40  19.10  10310.0  15.0   0.00  
2533  0.06   7.80  -0.64  5845.0  -9.60  35.20  10275.0 -35.0   0.00  
2534  0.25   7.72  -0.89  5845.0 -19.60  34.20  10245.0 -30.0   0.05  
2535  0.54  13.07   9.15  5820.0   1.95  39.35  10220.0 -25.0   0.00  

[2536 rows x 72 columns]

In [13]:
count_zeros = np.count_nonzero(dummy == 0)

print("Jumlah angka 0 dalam dataset:", count_zeros)

Jumlah angka 0 dalam dataset: 17215


In [14]:
euc_dist = {}

In [15]:
for i in range(dummy.shape[1]):
    print("Kolom :",i+1)
    current = dummy.index[dummy.iloc[:,i] == 0].tolist()
    for x in current:
        jarak(dummy,i)
        Final(dummy,i,3)

Kolom : 1
[1.1, 0.4, 1.1]
mean :  0.8666666666666667
standar deviasi :  0.32998316455372223
fuzzy :  [(1.1, 0.778820970680917), (0.4, 0.3679175864606329), (1.1, 0.778820970680917)]
fuzzy :  None
pembilang :  1.8605731700822707
penyebut :  1.9255595278224669
rata-rata tertimbang :  0.9662506628326955
 
[0.0, 0.4, 4.6]
mean :  1.6666666666666667
standar deviasi :  2.0805982045769644
fuzzy :  [(0.0, 0.7255620937026971), (0.4, 0.8308557704986), (4.6, 0.3701907779414984)]
fuzzy :  None
pembilang :  2.0352198867303324
penyebut :  1.9266086421427955
rata-rata tertimbang :  1.0563743160970867
 
[0.5, 0.4, 0.3]
mean :  0.39999999999999997
standar deviasi :  0.08164965809277261
fuzzy :  [(0.5, 0.47240328690554545), (0.4, 1.0), (0.3, 0.47240328690554595)]
fuzzy :  None
pembilang :  0.7779226295244366
penyebut :  1.9448065738110913
rata-rata tertimbang :  0.4
 
[1.2, 1.7, 0.2]
mean :  1.0333333333333334
standar deviasi :  0.6236095644623235
fuzzy :  [(1.2, 0.9649195174720684), (1.7, 0.564751581505

[0.0, 0.1, 1.1]
mean :  0.4000000000000001
standar deviasi :  0.496655480858378
fuzzy :  [(0.0, 0.7230400262651471), (0.1, 0.833256703302925), (1.1, 0.3704116739579805)]
fuzzy :  None
pembilang :  0.49077851168407116
penyebut :  1.9267084035260527
rata-rata tertimbang :  0.25472381331077476
 
[0.0, 2.4, 0.1]
mean :  0.8333333333333334
standar deviasi :  1.1085526098877259
fuzzy :  [(0.0, 0.75388123790523), (2.4, 0.36841685724583273), (0.1, 0.8034953964823135)]
fuzzy :  None
pembilang :  0.9645499970382299
penyebut :  1.9257934916333763
rata-rata tertimbang :  0.5008584779358349
 
[0.0, 1.0, 2.8]
mean :  1.2666666666666666
standar deviasi :  1.1585431464655178
fuzzy :  [(0.0, 0.5501192814145703), (1.0, 0.9738603926751792), (2.8, 0.4165549034722619)]
fuzzy :  None
pembilang :  2.1402141223975124
penyebut :  1.9405345775620115
rata-rata tertimbang :  1.1028992459832219
 
[0.0, 1.3, 1.3]
mean :  0.8666666666666667
standar deviasi :  0.6128258770283412
fuzzy :  [(0.0, 0.3679175864606329), (

[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 2.4]
mean :  0.7999999999999999
standar deviasi :  1.131370849898476
fuzzy :  [(0.0, 0.778820970680917), (0.0, 0.778820970680917), (2.4, 0.3679175864606327)]
fuzzy :  None
pembilang :  0.8830022075055185
penyebut :  1.9255595278224669
rata-rata tertimbang :  0.45856915600218706
 
[0.0, 0.45856915600218706, 0.0]
mean :  0.15285638533406234
standar deviasi :  0.21617157323475886
fuzzy :  [(0.0, 0.778820970680917), (0.45856915600218706, 0.36791758646063283), (0.0, 0.778820970680917)]
fuzzy :  None
pembilang :  0.16871565710161407
penyebut :  1.9255595278224669
rata-rata tertimbang :  0.0876190295152326
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.08

[0.0, 0.016741410172721224, 0.0]
mean :  0.0055804700575737415
standar deviasi :  0.007891976439837751
fuzzy :  [(0.0, 0.778820970680917), (0.016741410172721224, 0.36791758646063283), (0.0, 0.778820970680917)]
fuzzy :  None
pembilang :  0.006159459224695079
penyebut :  1.9255595278224669
rata-rata tertimbang :  0.003198789305496335
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 2.4]
mean :  0.7999999999999999
standar deviasi :  1.131370849898476
fuzzy :  [(0.0, 0.778820970680917), (0.0, 0.778820970680917), (2.4, 0.3679175864606327)]
fuzzy :  None
pembilang :  0.8830022075055185
penyebut :  1.9255595278224669
rata-rata tertimbang :  0.45856915600218706
 
[0.0, 0.45856915600218706, 0.0]
mean :  0.15285638533406234
standar deviasi :  0.21617157323475886
fuzzy :  [(0.0, 0.778820970680917), (0.45856915600218706, 0.36791758646063283), (0.0, 0.

[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.016990472229221433, 0.00011678117273803912]
mean :  0.005702417800653157
standar deviasi :  0.007982002215288945
fuzzy :  [(0.0, 0.7747894446776781), (0.016990472229221433, 0.3679307109975221), (0.00011678117273803912, 0.782845548205891)]
fuzzy :  None
pembilang :  0.006342738148673334
penyebut :  1.9255657038810914
rata-rata tertimbang :  0.0032939609050416565
 
[0.0, 0.0006111942133542818, 0.000912409822563425]
mean :  0.000507868011972569
standar deviasi :  0.00037958762624417904
fuzzy :  [(0.0, 0.4086248080767129), (0.0006111942133542818, 0.9636334114812103), (0.000912409822563425, 0.566747015990864)]
fuzzy :  None
pembilang :  0.0011060727091907361
penyebut :  1.939005235548787
rata-rata tertimbang :  0.0005704330699641922
 
[0.0, 0.0005704330699641922, 0.0]
mean :  0.00019014435665473073
st

...

[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0

[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0

[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0

[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0

[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0]
mean :  0.0
standar deviasi :  0.0
median :  2
fuzzy :  [(0

In [16]:
dummy

WSR0  WSR1  WSR2  WSR3  WSR4  WSR5  WSR6  WSR7  WSR8  WSR9  ...   T50  \
0      0.8   1.8   2.4   2.1   2.0   2.1   1.5   1.7   1.9   2.3  ... -15.5   
1      2.8   3.2   3.3   2.7   3.3   3.2   2.9   2.8   3.1   3.4  ... -14.5   
2      2.9   2.8   2.6   2.1   2.2   2.5   2.5   2.7   2.2   2.5  ... -15.9   
3      4.7   3.8   3.7   3.8   2.9   3.1   2.8   2.5   2.4   3.1  ... -16.8   
4      2.6   2.1   1.6   1.4   0.9   1.5   1.2   1.4   1.3   1.4  ... -16.8   
...    ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   ...   
2531   0.3   0.4   0.5   0.5   0.2   0.3   0.4   0.4   1.3   2.2  ... -12.4   
2532   1.0   1.4   1.1   1.7   1.5   1.7   1.8   1.5   2.1   2.4  ... -12.0   
2533   0.8   0.8   1.2   0.9   0.4   0.6   0.8   1.1   1.5   1.5  ... -11.8   
2534   1.3   0.9   1.5   1.2   1.6   1.8   1.1   1.0   1.9   2.0  ... -10.8   
2535   1.5   1.3   1.8   1.4   1.2   1.7   1.6   1.4   1.6   3.0  ... -11.9   

      RH50    U50    V50    HT50     KI     TT           SLP       SLP_  Precp  
0     0.15  10.67  -1.56  5795.0 -12.10  17.90  10330.000000 -55.000000   0.00  
1     0.48   8.39   3.84  5805.0  14.05  29.00  10275.000000 -55.000000   0.00  
2     0.60   6.94   9.80  5790.0  17.90  41.30  10235.000000 -40.000000   0.00  
3     0.49   8.73  10.54  5775.0  31.15  51.70  10195.000000 -40.000000   2.08  
4     0.49   8.73  10.54  5775.0  31.15  51.70  10195.655666 -21.311331   0.58  
...    ...    ...    ...     ...    ...    ...           ...        ...    ...  
2531  0.07   7.93  -4.41  5800.0 -25.60  21.80  10295.000000  65.000000   0.00  
2532  0.04   5.95  -1.14  5845.0 -19.40  19.10  10310.000000  15.000000   0.00  
2533  0.06   7.80  -0.64  5845.0  -9.60  35.20  10275.000000 -35.000000   0.00  
2534  0.25   7.72  -0.89  5845.0 -19.60  34.20  10245.000000 -30.000000   0.05  
2535  0.54  13.07   9.15  5820.0   1.95  39.35  10220.000000 -25.000000   0.00  

[2536 rows x 72 columns]

In [17]:
dummy.describe()

WSR0          WSR1          WSR2          WSR3          WSR4  \
count  2.536000e+03  2.536000e+03  2.536000e+03  2.536000e+03  2.536000e+03   
mean   1.506654e+00  1.457908e+00  1.422702e+00  1.403058e+00  1.402135e+00   
std    1.268675e+00  1.263291e+00  1.233104e+00  1.201012e+00  1.195168e+00   
min    7.602897e-07  1.573747e-07  6.652535e-07  7.263446e-08  6.052871e-08   
25%    5.000000e-01  4.280967e-01  4.473348e-01  4.000000e-01  4.502914e-01   
50%    1.200000e+00  1.100000e+00  1.100000e+00  1.100000e+00  1.100000e+00   
75%    2.200000e+00  2.100000e+00  2.100000e+00  2.100000e+00  2.100000e+00   
max    7.500000e+00  7.700000e+00  7.100000e+00  7.300000e+00  7.200000e+00   

               WSR5          WSR6          WSR7          WSR8          WSR9  \
count  2.536000e+03  2.536000e+03  2.536000e+03  2.536000e+03  2.536000e+03   
mean   1.422561e+00  1.506772e+00  1.878249e+00  2.326195e+00  2.617316e+00   
std    1.172222e+00  1.172199e+00  1.216096e+00  1.298096e+00  1.365068e+00   
min    6.052871e-08  7.868733e-08  8.236471e-07  1.815861e-07  2.300091e-07   
25%    5.000000e-01  6.000000e-01  1.000000e+00  1.400000e+00  1.700000e+00   
50%    1.200000e+00  1.300000e+00  1.700000e+00  2.300000e+00  2.600000e+00   
75%    2.000000e+00  2.100000e+00  2.600000e+00  3.200000e+00  3.500000e+00   
max    7.400000e+00  7.400000e+00  7.500000e+00  9.200000e+00  8.500000e+00   

       ...          T50         RH50          U50          V50         HT50  \
count  ...  2536.000000  2536.000000  2536.000000  2536.000000  2536.000000   
mean   ...   -10.213277     0.294993     9.640381     0.828346  5670.797154   
std    ...     4.138894     0.249023     9.441940     7.117383   841.219379   
min    ...   -24.800000     0.000023   -14.920000   -25.990000     0.277355   
25%    ...   -13.200000     0.090000     2.210000    -3.442500  5765.000000   
50%    ...    -9.850000     0.210000     8.825000     0.387944  5830.000000   
75%    ...    -7.000000     0.460000    16.472500     4.560000  5880.000000   
max    ...    -0.000754     1.000000    42.360000    30.420000  5965.000000   

                KI           TT           SLP         SLP_        Precp  
count  2536.000000  2536.000000   2536.000000  2536.000000  2536.000000  
mean     10.166225    36.286542   9936.975745     0.012685     0.371439  
std      20.403604    12.424028   1369.153346    35.185019     1.317001  
min     -56.700000   -10.100000     20.215236  -135.000000     0.000000  
25%      -3.125000    30.575000  10125.000000   -20.000000     0.000000  
50%      13.625000    40.700000  10155.000000    -1.910705     0.000000  
75%      27.800000    45.000000  10190.000000    15.000000     0.050000  
max      42.050000    59.150000  10350.000000   140.000000    20.650000  

[8 rows x 72 columns]

# Klasifikasi

In [18]:
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import confusion_matrix
from sklearn.metrics import accuracy_score

In [19]:
x = dummy.values
y = df.iloc[:, -1].values

In [20]:
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.25, random_state=0)

In [21]:
scaler = MinMaxScaler()
x_train = scaler.fit_transform(x_train)
x_test = scaler.transform(x_test)

In [22]:
classifier = KNeighborsClassifier(n_neighbors=3, metric='euclidean')
classifier.fit(x_train, y_train)
y_pred = classifier.predict(x_test)
cm = confusion_matrix(y_test, y_pred)
accuracy = accuracy_score(y_test, y_pred)
print(cm)
print(accuracy)

[[611   4]
 [ 15   4]]
0.9700315457413249


C:\Users\User\anaconda3\lib\site-packages\sklearn\neighbors\_classification.py:228: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set `keepdims` to True or False to avoid this warning.
  mode, _ = stats.mode(_y[neigh_ind, k], axis=1)


In [23]:
classifier = KNeighborsClassifier(n_neighbors=5, metric='euclidean')
classifier.fit(x_train, y_train)
y_pred = classifier.predict(x_test)
cm = confusion_matrix(y_test, y_pred)
accuracy = accuracy_score(y_test, y_pred)
print(cm)
print(accuracy)

[[614   1]
 [ 15   4]]
0.9747634069400631


C:\Users\User\anaconda3\lib\site-packages\sklearn\neighbors\_classification.py:228: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set `keepdims` to True or False to avoid this warning.
  mode, _ = stats.mode(_y[neigh_ind, k], axis=1)


In [24]:
classifier = KNeighborsClassifier(n_neighbors=7, metric='euclidean')
classifier.fit(x_train, y_train)
y_pred = classifier.predict(x_test)
cm = confusion_matrix(y_test, y_pred)
accuracy = accuracy_score(y_test, y_pred)
print(cm)
print(accuracy)

C:\Users\User\anaconda3\lib\site-packages\sklearn\neighbors\_classification.py:228: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set `keepdims` to True or False to avoid this warning.
  mode, _ = stats.mode(_y[neigh_ind, k], axis=1)


[[613   2]
 [ 19   0]]
0.9668769716088328


In [25]:
classifier = KNeighborsClassifier(n_neighbors=9, metric='euclidean')
classifier.fit(x_train, y_train)
y_pred = classifier.predict(x_test)
cm = confusion_matrix(y_test, y_pred)
accuracy = accuracy_score(y_test, y_pred)
print(cm)
print(accuracy)

[[614   1]
 [ 19   0]]
0.9684542586750788


C:\Users\User\anaconda3\lib\site-packages\sklearn\neighbors\_classification.py:228: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set `keepdims` to True or False to avoid this warning.
  mode, _ = stats.mode(_y[neigh_ind, k], axis=1)
